# Ceci est la partie 1 des TPs d'OASIS.
Le texte du TP est dans un fichier pdf et distribué par l'enseignant.

 techniquement: Lancer la première cellule sans y réfléchir.
 Les cellules d'après sont référencées en fonction des sections du TP et vous aident à réaliser ce qui est demandé par le sujet du TP.
  


In [3]:
!pip install simpleaudio # commenter si vous avez déjà installé simpleaudio
import numpy as np
import simpleaudio as sa
from IPython.display import Audio,display
import sys
import tempfile
import IPython
from skimage.transform import rescale
import matplotlib.pyplot as plt
import subprocess
import scipy.io as io
import scipy
# simplification de certains noms.
pi=np.pi
sin=np.sin
exp=np.exp
cos=np.cos
log=np.log



Notebook=True #mettre False pour un python standard (pas notebook)



def joue_son(s,Fe=44100):
  """Joue un son et tient compte de la variable globale Notebook
   Le son est normalisé et joué à la fréquence d'échantillonnage Fe qui vaut
   44100 par défaut."""
  if len(s.shape)>1:
    print("joue_son erreur: Le son n'est pas mono!")
    return
  if not Notebook:
    son=s.copy().astype(np.float32)
    sm=(abs(son)).max()
    if sm==0:
      print("Attention: son uniformément nul!")
    else:
      son/=sm # normalisation
      son=son*(2**15-1)
    son=son.astype(np.uint16)
    play_obj = sa.play_buffer(son, 1, 2, Fe)
    play_obj.wait_done()
  else: # on est dans un notebook ou colab
    son=s.copy().astype(np.float32)
    sm=(abs(son)).max()
    if sm==0:
      print("Attention: son uniformément nul!")
    else:
      son/=sm # normalisation
    wm=Audio(son, rate=Fe, autoplay=False)
    display(wm)


def viewimage(im, normalize=True,zoom=1,order=0,titre='',displayfilename=False):
    imin=im.copy().astype(np.float32)
    if len(im.shape)>2:
      imin = rescale(imin, zoom, order=order, channel_axis=2)
    else:
      imin = rescale(imin, zoom, order=order)
    if normalize:
        imin-=imin.min()
        if imin.max()>0:
            imin/=imin.max()
    else:
        imin=imin.clip(0,255)/255
    imin=(imin*255).astype(np.uint8)
    filename=tempfile.mktemp(titre+'.png')
    if displayfilename:
        print (filename)
    plt.imsave(filename, imin, cmap='gray')
    IPython.display.display(IPython.display.Image(filename))

def charge_image(fich):
    a=np.float32(plt.imread(fich))
    return a


def lire_fichier_son(fichier):
  f=io.wavfile.read(fichier)
  if len(f[1].shape)>1:
    out=f[1][:,0] #pas de stereo
  else:
    out=f[1]
  Fe=f[0]
  return (out,Fe) # renvoie un canal sonore (pas de   stereo) et la Freq. d'echant. Fe

lien_donnees="https://www.telecom-paris.fr/perso/~ladjal/donnees_tp1_oasis.tgz"
fichier="donnees_tp1_oasis.tgz"
repdonnees="donnees_tp1_oasis/"
if not (lien_donnees is None):
  subprocess.run(["wget","-O",fichier,lien_donnees])
  subprocess.run(["tar","-xvzf",fichier])



ERROR: Invalid requirement: '#'


FileNotFoundError: [WinError 2] Le fichier spécifié est introuvable

# Lecture d'un son depuis le disque

In [ ]:
#exemple de lecture de son et le jouer.
#%%
fichier='handel.wav'
#fichier='oiseau.wav'
#fichier='marche.wav'

son,Fe=lire_fichier_son(repdonnees+fichier)
joue_son(son,Fe=Fe)


# Écoute d'un écho

In [ ]:
# Echo avec 0.1s

# On utilise la fonction np.convolve pour convoluer le son avec un h d'écho

Fe=44100
temps_echo=0.1 #Temps d'écho
pos_echo=int(temps_echo*Fe) # Par quoi multiplier le temps pour obtenir une position dans Z
h=np.zeros(pos_echo)
h[0]=1
h[-1]=0.8

son_avec_echo=np.convolve(son,h)
joue_son(son_avec_echo)


In [ ]:
# Echo avec 0.5s

# On utilise la fonction np.convolve pour convoluer le son avec un h d'écho

Fe=44100
temps_echo=0.5 #Temps d'écho
pos_echo=int(temps_echo*Fe) # Par quoi multiplier le temps pour obtenir une position dans Z
h=np.zeros(pos_echo)
h[0]=1
h[-1]=0.8

son_avec_echo=np.convolve(son,h)
joue_son(son_avec_echo)


In [ ]:
# Echo avec 0.8s

# On utilise la fonction np.convolve pour convoluer le son avec un h d'écho

Fe=44100
temps_echo=0.8 #Temps d'écho
pos_echo=int(temps_echo*Fe) # Par quoi multiplier le temps pour obtenir une position dans Z
h=np.zeros(pos_echo)
h[0]=1
h[-1]=0.8

son_avec_echo=np.convolve(son,h)
joue_son(son_avec_echo)


Q1: 
Complexité du calcul réalisé :
On a N = pos_echo    opérations pour la convolution par terme du fichier son

Et la convolution est réalisée Nt fois, Nt = Fe * Durée du son 

On a donc au total une complexité en O(N.NT), qui dépend de t1

Il n'est toutefois pas nécessaire de réaliser toutes les opérations de convolution, les termes de h étant tous nuls sauf h[0] et h[-1]
On aurait donc  O(NT) qui ne dépend plus de t1

In [1]:
# écoute d'une onde
exp=np.exp
i=1j
pi=np.pi
n=np.arange(0,100000)
f=0.01
u=exp(2*i*pi*f * n)
joue_son(np.real(u),44100)
joue_son(np.real(u),22050)

NameError: name 'np' is not defined

Q2 : Première fréquence de 44100*0.01=441Hz

Deuxième fréquence de 22050*0.01=220.5Hz

In [ ]:
#Definition des filtres rejecteurs
lfilter=scipy.signal.lfilter
def rejette1(entree,f0,Fe):

#valeur recommandee pour rho: au moins 0.9 et jamais plus de 1

    z0=exp(2*1j*pi*f0/Fe); # position sur le cercle unite de la frequence a eliminer

    sortie=lfilter([1 ,-z0],1,entree.astype(np.float32));

    sortie=lfilter([1, -np.conj(z0)],1,sortie); #Le signal est reel, il faut donc eliminer -f0 aussi!


    sortie=np.real(sortie);# En raison d'erreurs d'arrondi il peut subsister une partie imaginaire
    return sortie


def rejette2(entree,f0,Fe,rho):

#valeur recommandee pour rho: au moins 0.9 et jamais plus de 1

    z0=exp(2*1j*pi*f0/Fe); # position sur le cercle unite de la frequence a eliminer

    sortie=lfilter([1 ,-z0],[1 ,-rho*z0],entree.astype(np.float32));

    sortie=lfilter([1, -np.conj(z0)],[1 ,-rho*np.conj(z0)],sortie); #Le signal est reel, il faut donc eliminer -f0 aussi!

    sortie=np.real(sortie);# En raison d'erreurs d'arrondi il peut subsister une partie imaginaire
    return sortie

def norme2(X): # renvoie la norme 2 d'une variable. Utile pour calculer des erreurs
  return ((((X).astype(np.float32))**2).sum())**0.5




In [ ]:
help(lfilter)

Help on function lfilter in module scipy.signal._signaltools:

lfilter(b, a, x, axis=-1, zi=None)
    Filter data along one-dimension with an IIR or FIR filter.
    
    Filter a data sequence, `x`, using a digital filter.  This works for many
    fundamental data types (including Object type).  The filter is a direct
    form II transposed implementation of the standard difference equation
    (see Notes).
    
    The function `sosfilt` (and filter design using ``output='sos'``) should be
    preferred over `lfilter` for most filtering tasks, as second-order sections
    have fewer numerical problems.
    
    Parameters
    ----------
    b : array_like
        The numerator coefficient vector in a 1-D sequence.
    a : array_like
        The denominator coefficient vector in a 1-D sequence.  If ``a[0]``
        is not 1, then both `a` and `b` are normalized by ``a[0]``.
    x : array_like
        An N-dimensional input array.
    axis : int, optional
        The axis of the input d

Pour effectuer une convolution d'un signal h contre un RIF on peut faire : lfilter(h, 1, x) où h est la réponse impulsionnelle et x le signal à convoluer.




In [ ]:
# Ici on ajoute un son parasite et on ecoute
f0=1261
y=son[:4*Fe] # le son de départ doit contenir au moins 4 secondes (sinon changer)
n=np.arange(len(y)); #le temps discret que dure le signal y
sonbruite=y+0.5*(abs(y).max())*np.cos(2*pi*f0/Fe*n); #on ajoute une onde parasite
joue_son(sonbruite,Fe=Fe)



Q 4: La fréquence réduite de l'onde parasite est u=f0/Fe = 1261/44100 = 0.03 environ

In [ ]:
# ecoute et evaluation de rejette1
sortie1=rejette1(sonbruite,f0,Fe)
joue_son(sortie1,Fe)
erreur1=norme2(sortie1-y)/norme2(y)
print ("erreur relative après rejette 1 en poucentage",erreur1*100)

erreur relative après rejette 1 en poucentage 98.05491982342085


Q5: La Transformée de Fourier sur Z du filtrage est :

Y(z) = 1 - conj(z0).z^(-1) - z0.z^(-1) + .z^(-2)

Q6: Signal toujours parasité, et très atténué

Q7: La Transformée de Fourier sur Z du filtrage est :

Y(z) = (1-z0.z^(-1)) / (1 - rho.z0.z^(-1)) . (1-conj(z0).z^(-1)) / (1 - rho.conj(z0).z^(-1))

Le signal est beaucoup plus clair

In [ ]:
# ecoute et evaluation de rejette2
sortie2=rejette2(sonbruite,f0,Fe,0.999)
joue_son(sortie2,Fe)
erreur2=norme2(sortie2-y)/norme2(y)
print ("erreur relative après rejette 2 en poucentage",erreur2*100)

erreur relative après rejette 2 en poucentage 10.163616125249934


Q8 : 
Pour rejette1:

Les zéros de la fonction sont z0 et conj(z0), pas de pôles

Pour rejette2 :

Les zéros sont z0 et conj(z0)
Et les pôles rho.conj(z0) et rho.conj(z0)

z0 = exp(2.i.pi.f0/Fe) = exp(2.i.pi.0.03)

La fonction rejette2 est plus sélective, le rendu est donc plus clair et mieux filtré

Q9 : Rho doit être strictement inférieur à 1 car sinon la transformée sur Z de Fourier contient un pôle de module strictement supérieur à 1, le système est alors instable.

Q10 : Pour rho trop proche de 1, la sélection du filtre ne peut pas traiter les fréquences proches de la fréquence cible différentes de celle-ci.